In [1]:
import torch
import torch.nn as nn
import torchvision.datasets as datasets
import torchvision.transforms as transforms
#from torch.autograd import Variable

In [2]:
input_size = 784
hidden_size = 400
out_size = 10
epochs = 10
batch_size = 100
learning_rate = 0.001

In [3]:
train_dataset = datasets.MNIST(root='./data',
                              train=True,
                              transform=transforms.ToTensor(),
                              download=True)

test_dataset = datasets.MNIST(root='./data',
                              train=False,
                              transform=transforms.ToTensor())

In [4]:
# inserting data into a loder class to makeit iterable
train_loader = torch.utils.data.DataLoader(dataset=train_dataset,
                                          batch_size=batch_size,
                                          shuffle=True)

test_loader = torch.utils.data.DataLoader(dataset=test_dataset,
                                          batch_size=batch_size,
                                          shuffle=False)


In [5]:
class Net(nn.Module):
    
    def __init__(self,input_size,hidden_size,out_size):
        super(Net,self).__init__()
        self.fc1 = nn.Linear(input_size,hidden_size)
        self.relu = nn.ReLU()
        self.fc2 = nn.Linear(hidden_size,hidden_size)
        self.fc3 = nn.Linear(hidden_size,out_size)
        
    def forward(self,x):
        out = self.fc1(x)
        out = self.relu(out)
        out = self.fc2(out)
        out = self.relu(out)
        out = self.fc3(out)
        
        return out
        

In [6]:
# Create a Net class object
net = Net(input_size,hidden_size,out_size)
CUDA = torch.cuda.is_available()
if CUDA:
    net = net.cuda()
    
# Select the loss function and optimization method
criterion = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(net.parameters(),lr=learning_rate)

In [7]:
for i, (images, labels) in enumerate(train_loader):
    print(images.view(-1,28*28))
    break

tensor([[0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.],
        ...,
        [0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.]])


In [14]:
# Train the network
correct_train = 0
total_train = 0

for epoch in range(epochs):
    for i, (images, labels) in enumerate(train_loader):
        # Flatten the image from (batch,1,28,28) --> (100,1,28,28), where 1 is the number of channels (grayscale --> 1) and wrap it in a variable
        #images = Variable(images.view(-1,28*28))
        #labels = Variable(labels)
        images = images.view(-1,28*28)
        
        # Send the images and the lables to our graphics card memory
        if CUDA:
            images = images.cuda()
            labels = labels.cuda()
        
        # Set the gradient to zero
        optimizer.zero_grad()
        # Pass our trainig set to the object net (which is the nn)
        outputs = net(images)
        _, predicted = torch.max(outputs.data,1) # We select the maximum value got and return its index
        
        total_train += labels.size(0)
        
        if CUDA:
            correct_train += (predicted.cpu() == labels.cpu()).sum()
        else:
            correct_train += (predicted == labels).sum()
        
        loss = criterion(outputs,labels) # Calculate the loss
        loss.backward() # Backpropagate
        optimizer.step() # Update the weights
        
        #if i+1 % 100 == 0:
        print("Epoch: [{}/{}], Iteration [{}/{}], Training Loss: {:.3f}, Training Accuracy: {:.3f}%".format
                  (epoch+1, epochs, i+1, len(train_dataset)//batch_size, loss.item(), (100*correct_train.double()/total_train)))
            
print("Done training!!!")

Epoch: [1/10], Iteration [1/600], Training Loss: 0.000, Training Accuracy: 100.000%
Epoch: [1/10], Iteration [2/600], Training Loss: 0.000, Training Accuracy: 100.000%
Epoch: [1/10], Iteration [3/600], Training Loss: 0.001, Training Accuracy: 100.000%
Epoch: [1/10], Iteration [4/600], Training Loss: 0.000, Training Accuracy: 100.000%
Epoch: [1/10], Iteration [5/600], Training Loss: 0.004, Training Accuracy: 100.000%
Epoch: [1/10], Iteration [6/600], Training Loss: 0.002, Training Accuracy: 100.000%
Epoch: [1/10], Iteration [7/600], Training Loss: 0.000, Training Accuracy: 100.000%
Epoch: [1/10], Iteration [8/600], Training Loss: 0.000, Training Accuracy: 100.000%
Epoch: [1/10], Iteration [9/600], Training Loss: 0.006, Training Accuracy: 100.000%
Epoch: [1/10], Iteration [10/600], Training Loss: 0.000, Training Accuracy: 100.000%
Epoch: [1/10], Iteration [11/600], Training Loss: 0.000, Training Accuracy: 100.000%
Epoch: [1/10], Iteration [12/600], Training Loss: 0.000, Training Accuracy

In [15]:
# Test the NN
correct = 0
total = 0

for images, labels in test_loader:
    images = images.view(-1,28*28)
    if CUDA:
        images = images.cuda()
        
    # for each input (sample/row) in the batch the output will contain 10 elements
    outputs = net(images)
    _, predicted = torch.max(outputs.data,1)
    
    total += labels.size(0)
    if CUDA:
        correct += (predicted.cpu() == labels.cpu()).sum()
    else:
        correct += (predicted == labels).sum()
    

print('Final test accuracy: %d %%' % (100*correct/total))
    

Final test accuracy: 97 %
